In [3]:
import gensim
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
pd.set_option('display.max_colwidth', 100)

In [35]:
data = pd.read_csv("train.tsv", sep="\t", on_bad_lines='skip')
data.head(5)

1  \
0  1   
1  0   
2  1   
3  0   
4  1   

  Mindaugas Budzinauskas wierzy w odbudowę formy Kevina Johnsona. Czy ktoś opuści Polpharmę? Mindaugas Budzinauskas w rozmowie z WP SportoweFakty opowiada o transferze Kevina Johnsona, ewentualnych odejściach z Polpharmy i kolejnym meczu PLK z Anwilem. - Potrzebowaliśmy takiego gracza, jak Johnson - podkreśla szkoleniowiec starogardzian.  
0  Przyjmujący reprezentacji Polski wrócił do PGE Skry Bełchatów Tylko rok trwał rozbrat Artura Sza...                                                                                                                                                                                                                                               
1  FEN 9: Zapowiedź walki Róża Gumienna vs Katarzyna Posiadała (wideo) Podczas Fight Exclusive Nigh...                                                                                                                                                                                                                                               
2  Aleksander Filipiak: Czuję się dobrze w nowym klubie Aleksander Filipiak w przerwie letniej zami...                                                                                                                                                                                                                                               
3  Victoria Carl i Aleksiej Czerwotkin mistrzami świata juniorów na 5 i 10 kilometrów Biegi na 5 i ...                                                                                                                                                                                                                                               
4  Świat poznał ją na mundialu. Francuska WAG czaruje pięknym ciałem Rachel Legrain-Trapani to jedn...

In [36]:
data.columns = ["label", "text"]
data.head(5)

label  \
0      1   
1      0   
2      1   
3      0   
4      1   

                                                                                                  text  
0  Przyjmujący reprezentacji Polski wrócił do PGE Skry Bełchatów Tylko rok trwał rozbrat Artura Sza...  
1  FEN 9: Zapowiedź walki Róża Gumienna vs Katarzyna Posiadała (wideo) Podczas Fight Exclusive Nigh...  
2  Aleksander Filipiak: Czuję się dobrze w nowym klubie Aleksander Filipiak w przerwie letniej zami...  
3  Victoria Carl i Aleksiej Czerwotkin mistrzami świata juniorów na 5 i 10 kilometrów Biegi na 5 i ...  
4  Świat poznał ją na mundialu. Francuska WAG czaruje pięknym ciałem Rachel Legrain-Trapani to jedn...

In [38]:
data['text_preprocessed'] = data['text'].apply(lambda x: gensim.utils.simple_preprocess(x))
data.head(5)

label  \
0      1   
1      0   
2      1   
3      0   
4      1   

                                                                                                  text  \
0  Przyjmujący reprezentacji Polski wrócił do PGE Skry Bełchatów Tylko rok trwał rozbrat Artura Sza...   
1  FEN 9: Zapowiedź walki Róża Gumienna vs Katarzyna Posiadała (wideo) Podczas Fight Exclusive Nigh...   
2  Aleksander Filipiak: Czuję się dobrze w nowym klubie Aleksander Filipiak w przerwie letniej zami...   
3  Victoria Carl i Aleksiej Czerwotkin mistrzami świata juniorów na 5 i 10 kilometrów Biegi na 5 i ...   
4  Świat poznał ją na mundialu. Francuska WAG czaruje pięknym ciałem Rachel Legrain-Trapani to jedn...   

                                                                                     text_preprocessed  
0  [przyjmujący, reprezentacji, polski, wrócił, do, pge, skry, bełchatów, tylko, rok, trwał, rozbra...  
1  [fen, zapowiedź, walki, róża, gumienna, vs, katarzyna, posiadała, wideo, podczas, fight, exclusi...  
2  [aleksander, filipiak, czuję, się, dobrze, nowym, klubie, aleksander, filipiak, przerwie, letnie...  
3  [victoria, carl, aleksiej, czerwotkin, mistrzami, świata, juniorów, na, kilometrów, biegi, na, k...  
4  [świat, poznał, ją, na, mundialu, francuska, wag, czaruje, pięknym, ciałem, rachel, legrain, tra...

In [39]:
from gensim.test.utils import common_texts
from gensim.models import Word2Vec

model = Word2Vec(sentences=data['text_preprocessed'], vector_size=100, window=5, min_count=1, workers=4)

In [40]:
import tensorflow as tf

token = tf.keras.preprocessing.text.Tokenizer(1234)
token.fit_on_texts(data['text_preprocessed'])
text = token.texts_to_sequences(data['text_preprocessed'])
text = tf.keras.utils.pad_sequences(text, 75)

In [41]:
X_train, X_test, y_train, y_test = train_test_split(np.array(text), data['label'], test_size=0.3)
X_train

array([[  0,   0,   0, ..., 189, 416, 346],
       [  0,   0,   0, ...,  56, 397, 907],
       [  0,   0,   0, ..., 137, 226, 343],
       ...,
       [  0,   0,   0, ..., 817,   3, 317],
       [  0,   0,   0, ..., 656,  20, 923],
       [  0,   0,   0, ...,   6, 478,  27]])

In [42]:
vocab_size = len(token.word_index) + 1
embedding_matrix = np.zeros((vocab_size, 100))

for word, i in token.word_index.items():
    if word in model.wv:
        embedding_matrix[i] = model.wv[word]
        
import keras



In [48]:
from keras.src.layers import Dropout, Dense, Activation, Embedding, MaxPooling1D, GlobalMaxPooling1D
from keras.src.layers import Conv1D
from keras import Sequential

opt = keras.optimizers.Adam(learning_rate=0.01)

keras_model = Sequential()
keras_model.add(Embedding(vocab_size, 100, weights=[embedding_matrix], trainable=False))
keras_model.add(Dropout(0.4))
keras_model.add(Conv1D(100, 3, activation='relu', padding='same', strides=1))
keras_model.add(Conv1D(100, 3, activation='relu', padding='same', strides=1))
keras_model.add(GlobalMaxPooling1D())
keras_model.add(Dropout(0.4))
keras_model.add(Dense(200))
keras_model.add(Activation('relu'))
keras_model.add(Dropout(0.4))
keras_model.add(Dense(1))
keras_model.add(Activation('sigmoid'))
keras_model.compile(loss='binary_crossentropy', metrics=['acc'], optimizer=opt)
keras_model.fit(X_train, y_train, batch_size=64, epochs=10, validation_data=(X_test, y_test))

Epoch 1/10
1074/1074 [==============================] - 45s 41ms/step - loss: 0.1928 - acc: 0.9313 - val_loss: 0.1255 - val_acc: 0.9564
Epoch 2/10
1074/1074 [==============================] - 43s 40ms/step - loss: 0.1985 - acc: 0.9309 - val_loss: 0.1173 - val_acc: 0.9543
Epoch 3/10
1074/1074 [==============================] - 44s 41ms/step - loss: 0.2170 - acc: 0.9252 - val_loss: 0.1254 - val_acc: 0.9522
Epoch 4/10
1074/1074 [==============================] - 44s 41ms/step - loss: 0.1953 - acc: 0.9291 - val_loss: 0.1191 - val_acc: 0.9524
Epoch 5/10
1074/1074 [==============================] - 44s 41ms/step - loss: 0.2065 - acc: 0.9253 - val_loss: 0.1237 - val_acc: 0.9503
Epoch 6/10
1074/1074 [==============================] - 43s 40ms/step - loss: 0.1990 - acc: 0.9275 - val_loss: 0.1334 - val_acc: 0.9452
Epoch 7/10
1074/1074 [==============================] - 44s 41ms/step - loss: 0.1960 - acc: 0.9256 - val_loss: 0.1266 - val_acc: 0.9516
Epoch 8/10
1074/1074 [==========================

In [49]:
model = keras_model

In [50]:
def preprocess(path):
    data = pd.read_csv(path, sep="\t", on_bad_lines='skip')
    data.columns = ["text"]
    data['text_clean'] = data['text'].apply(lambda x: gensim.utils.simple_preprocess(x))
    text = token.texts_to_sequences(data['text_clean'])
    text = tf.keras.utils.pad_sequences(text, 75)
    return text

In [51]:
x = preprocess("in.tsv")
res = model.predict(x)
y_predictions = np.where(res >= 0.49, 1, 0)
out = pd.DataFrame(y_predictions)

171/171 [==============================] - 2s 8ms/step


In [53]:
y_predictions = np.where(res>=0.49, 1, 0) 

In [54]:
out = pd.DataFrame(y_predictions)

In [55]:
print(out)

      0
0     1
1     1
2     0
3     1
4     1
...  ..
5439  1
5440  1
5441  1
5442  0
5443  1

[5444 rows x 1 columns]


In [56]:
out.to_csv('out.tsv', sep="\t", index=False) 